In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
#import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


INFO:numexpr.utils:Note: NumExpr detected 32 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [7]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP

from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

def get_atac_values(resolution):
    species='mouse'
    base_folder='/grid/gillis/data_norepl/lohia/'
    SRP_name='aggregates'

    cell_type_map = {'VLMC' : 'VLMC' ,
    'Micro-PVM' : 'MGC' ,
    'Astro' : 'ASC' ,
    'L2/3 IT' : 'L2_3_IT' ,
    'L5 IT' : 'L5_IT' ,
    'Oligo' : 'ODC' ,
    'Sst' : 'SST' ,
    'Pvalb' : 'PVALB' ,
    'Vip' : 'VIP' ,
    'Endo' : 'Endo' ,
    'Lamp5' : 'LAMP5' ,
    'Sncg' : 'SNCG' ,
    'L5/6 NP' : 'L5_6_NP' ,
    'L5 ET' : 'L5_ET' ,
    'L6 CT' : 'L6_CT' ,
    'L6b' :  'L6b' ,
    'Sst Chodl' : 'SST' ,
    'L6 IT' : 'L6_IT' 
    }



    df_marker = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/marker_all_info.csv')

    df_marker = df_marker.drop_duplicates('group')

    class_dict = dict(zip(df_marker.group, df_marker.classt))

    df_atac_subclass_macs2 = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/zemke_2023/Supplementary_Table_7.tsv', sep='\t')



    df_atac_subclass_macs2['chr'] = [x.split('-')[0] for x in df_atac_subclass_macs2['coord']]
    df_atac_subclass_macs2['st'] = [x.split('-')[1] for x in df_atac_subclass_macs2['coord']]
    df_atac_subclass_macs2['end'] = [x.split('-')[2] for x in df_atac_subclass_macs2['coord']]
    df_atac_subclass_macs2 = df_atac_subclass_macs2[~df_atac_subclass_macs2['chr'].isin(['chrX', 'chrY'])]
    df_atac_subclass_macs2['chr_num'] = [int(x.split('chr')[1]) for x in df_atac_subclass_macs2['chr']]
    df_atac_subclass_macs2['ste'] = df_atac_subclass_macs2['st'].astype('int')
    df_atac_subclass_macs2 = df_atac_subclass_macs2.sort_values(['chr_num', 'ste'])



    df_list = []
    for keyl in cell_type_map.keys():

        df_atac_subclass_macs2['gg'] = [1 if cell_type_map[keyl] in x else 0 for x in df_atac_subclass_macs2['celltype']]
        df = df_atac_subclass_macs2[df_atac_subclass_macs2['gg'] == 1]
        df['cell_type'] = keyl
        df_list.append(df[['chr', 'st', 'end', 'peak_id', 'cell_type']])
    df_Zemke2023_label = pd.concat(df_list)

    df_Zemke2023_label = df_Zemke2023_label.drop_duplicates()
    b_dir = f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/zemke_2023/'

    df_Zemke2023_label.to_csv(f'{b_dir}/all_cre_{resolution}.bed', index=False, header=False, sep='\t')

    os.system(f"bedtools intersect -wo -b {b_dir}/all_cre_{resolution}.bed -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {b_dir}/all_cre_bins_{resolution}.bed")

    df_Zemke2023 = pd.read_csv(f'{b_dir}/all_cre_bins_{resolution}.bed', sep='\t', names=['chr', 'st', 'end', 'bin_id', 'p_chr', 'p_st', 'p_end', 'peak_label', 'cell_type', 'overlap' ])

    df_Zemke2023['rank'] = 1






    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['overlap'] > 250]
    #df_Zemke2023 = df_Zemke2023.sort_values( by=['overlap'], ascending=False).drop_duplicates(subset=['bin_id'])

    #df_Zemke2023['cell_type'] = [class_dict[x] if x in class_dict.keys() else 'del' for x in df_Zemke2023['cell_type'].tolist()]

    df_Zemke2023_table = df_Zemke2023.pivot_table(index='bin_id', columns='cell_type', values='rank', aggfunc='sum')

    df_Zemke2023_table.fillna(0, inplace=True)

    df_Zemke2023_table[df_Zemke2023_table != 0] = 1

    df_Zemke2023_mouse = df_Zemke2023_table.T
    
    print (df_Zemke2023_mouse)

    #df_Zemke2023_mouse = df_Zemke2023_table[~df_Zemke2023_table.index.isin(['del'])]




    adata = ad.AnnData(df_Zemke2023_mouse)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/zemke_brain.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path








    #z_score_human
    species='human'

    cell_type_map = {'VLMC' : 'VLMC' ,
    'Micro-PVM' : 'MGC' ,
    'Astro' : 'ASC' ,
    'L2/3 IT' : 'L2_3_IT' ,
    'L5 IT' : 'L5_IT' ,
    'Oligo' : 'ODC' ,
    'Sst' : 'SST' ,
    'Pvalb' : 'PVALB' ,
    'Vip' : 'VIP' ,
    'Endo' : 'Endo' ,
    'Lamp5' : 'LAMP5' ,
    'Sncg' : 'SNCG' ,
    'L5/6 NP' : 'L5_6_NP' ,
    'L5 ET' : 'L5_ET' ,
    'L6 CT' : 'L6_CT' ,
    'L6b' :  'L6b' ,
    'Sst Chodl' : 'SST' ,
    'L6 IT' : 'L6_IT' 
    }

    df_atac_subclass_macs2 = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/zemke_2023/Supplementary_Table_4.tsv', sep='\t')



    df_atac_subclass_macs2['chr'] = [x.split('-')[0] for x in df_atac_subclass_macs2['hg38_coord']]
    df_atac_subclass_macs2['st'] = [x.split('-')[1] for x in df_atac_subclass_macs2['hg38_coord']]
    df_atac_subclass_macs2['end'] = [x.split('-')[2] for x in df_atac_subclass_macs2['hg38_coord']]
    df_atac_subclass_macs2 = df_atac_subclass_macs2[~df_atac_subclass_macs2['chr'].isin(['chrX', 'chrY'])]
    df_atac_subclass_macs2['chr_num'] = [int(x.split('chr')[1]) for x in df_atac_subclass_macs2['chr']]
    df_atac_subclass_macs2['ste'] = df_atac_subclass_macs2['st'].astype('int')
    df_atac_subclass_macs2 = df_atac_subclass_macs2.sort_values(['chr_num', 'ste'])



    df_list = []
    for keyl in cell_type_map.keys():

        df_atac_subclass_macs2['gg'] = [1 if cell_type_map[keyl] in x else 0 for x in df_atac_subclass_macs2['celltype']]
        df = df_atac_subclass_macs2[df_atac_subclass_macs2['gg'] == 1]
        df['cell_type'] = keyl
        df_list.append(df[['chr', 'st', 'end', 'peak_id', 'cell_type']])
    df_Zemke2023_label = pd.concat(df_list)

    df_Zemke2023_label = df_Zemke2023_label.drop_duplicates()




    b_dir = f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/zemke_2023/'

    df_Zemke2023_label.to_csv(f'{b_dir}/all_cre_{resolution}.bed', index=False, header=False, sep='\t')


    os.system(f"bedtools intersect -wo -b {b_dir}/all_cre_{resolution}.bed -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {b_dir}/all_cre_bins_{resolution}.bed")

    df_Zemke2023 = pd.read_csv(f'{b_dir}/all_cre_bins_{resolution}.bed', sep='\t', names=['chr', 'st', 'end', 'bin_id', 'p_chr', 'p_st', 'p_end', 'peak_label', 'cell_type', 'overlap' ])

    df_Zemke2023['rank'] = 1

    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['overlap'] > 250]


    df_marker = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/marker_all_info.csv')

    df_marker = df_marker.drop_duplicates('group')

    class_dict = dict(zip(df_marker.group, df_marker.classt))

    df_Zemke2023['group'] = [class_dict[x] if x in class_dict.keys() else 'del' for x in df_Zemke2023['cell_type'].tolist()]


    #df = df[df['subclass'].isin(['Glial & Endo', 'VLMC'])]
    #df = df[df['subclass'].isin(['CGE-derived', 'MGE-derived'])]
    #df = df[df['subclass'].isin(['IT-derived', 'Non-IT-derived'])]
    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['cell_type'].isin(df['cell_type'].tolist())]
    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['group']=='Glutamatergic']

    df_Zemke2023_table = df_Zemke2023.pivot_table(index='bin_id', columns='cell_type', values='rank', aggfunc='sum')

    df_Zemke2023_table.fillna(0, inplace=True)

    df_Zemke2023_table[df_Zemke2023_table != 0] = 1

    df_Zemke2023_human = df_Zemke2023_table.T
    #df_Zemke2023_human = df_Zemke2023_table[~df_Zemke2023_table.index.isin(['del'])]

    adata = ad.AnnData(df_Zemke2023_human)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/zemke_brain.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path





    df_heart = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/hocker_heart/heart_table_s6.tsv', sep='\t', skiprows=1)
    df_heart.to_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/hocker_heart/heart.bed',header=False, index=False, sep='\t')

    os.system(f"bedtools intersect -wo -a {base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/hocker_heart/heart.bed -b {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/cre_modules_heart.bed")
    df_hba_modules = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/cre_modules_heart.bed', sep='\t', names=['a', 'b','c' ,'logfc', 'p_val', 'cell_type', 'chr', 'start', 'end', 'bin_id', 'overlap'])


    #df_hba_modules = df_hba_modules[df_hba_modules['overlap'] > 250]

    df_hocker_table = df_hba_modules.pivot_table(index='bin_id', columns='cell_type', values='logfc', aggfunc='sum')

    df_hocker_table.fillna(0, inplace=True)

    df_hocker_table[df_hocker_table != 0] = 1

    df_hocker_human = df_hocker_table.T

    adata = ad.AnnData(df_hocker_human)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/zemke_heart.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path
    
    import pyBigWig



    name_category_dict = {
        'Astro-NT_NN': 'Astro',
        'Lamp5_Gaba': 'Lamp5',
        'Astro-TE_NN': 'Astro',
        'Lamp5_Lhx6_Gaba': 'Lamp5_Lhx6',
        'Endo_NN': 'Endo',
        'Microglia_NN': 'Micro-PVM',
        'L2_3_IT_CTX_Glut': 'L2/3 IT',
        'Oligo_NN': 'Oligo',
        'L4_5_IT_CTX_Glut': 'L4/5 IT',
        'OPC_NN': 'OPC',
        'L4_RSP-ACA_Glut': 'L4 RSP-ACA',
        'Peri_NN': 'Peri',
        'L5_ET_CTX_Glut': 'L5 ET',
        'Pvalb_chandelier_Gaba': 'Chandelier',
        'L5_IT_CTX_Glut': 'L5 IT',
        'Pvalb_Gaba': 'Pvalb',
        'L5_NP_CTX_Glut': 'L5 NP',
        'Sncg_Gaba': 'Sncg',
        'L6b_CTX_Glut': 'L6b',
        'Sst_Gaba': 'Sst',
        'L6_CT_CTX_Glut': 'L6 CT',
        'Vip_Gaba': 'Vip',
        'L6_IT_CTX_Glut': 'L6 IT',
        'VLMC_NN': 'VLMC'
    }

    species='mouse'
    SRP_name='aggregates'


    compartment_list  = []

    for f_name, f_mapped in zip(name_category_dict.keys(), name_category_dict.values()):

        f_path = "/grid/gillis/data_norepl/lohia/BICCN_enhancer_challenege/liu-2023-sn3c/compartment_score/"

        m_p = f"{f_path}/{f_name}.compartment_score.100K.bw"

        bw_file = pyBigWig.open(m_p)



        bedgraph_file = f'/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/your_output_file.bedgraph'

        # Open the BedGraph file for writing
        with open(bedgraph_file, 'w') as f:
            for chrom in bw_file.chroms():
                # Iterate over each chromosome in the BigWig file
                intervals = bw_file.intervals(chrom)
                for interval in intervals:
                    # Write each interval to the BedGraph file
                    f.write(f"{chrom}\t{interval[0]}\t{interval[1]}\t{interval[2]}\n")


        # Close the BigWig file
        bw_file.close()

        os.system(f"bedtools intersect -wo -b /grid/gillis/data_norepl/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/your_output_file.bedgraph -a /grid/gillis/data_norepl/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {f_path}/intersect_{resolution}.bed")


        enhancer_bins = pd.read_csv(f'{f_path}/intersect_{resolution}.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'compartment_score', 'overlap'])
        enhancer_bins['cell_type'] = f_mapped
        compartment_list.append(enhancer_bins)



    compartment_matrix = pd.concat(compartment_list)



    compartment_df = compartment_matrix.pivot_table(columns='bin_id', index='cell_type', values='compartment_score', aggfunc='mean')


    adata = ad.AnnData(compartment_df)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/compartment.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path
    

In [8]:
for resolution in ['10kbp_raw', '1kbp_raw', '100kbp_raw', '250kbp_raw']:
    get_atac_values(resolution)

<ipython-input-7-a859723120c3>:80: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:80: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:80: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-

bin_id     309     311     312     313     316     318     319     320     \
cell_type                                                                   
Astro         0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
Endo          0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
L2/3 IT       1.0     1.0     1.0     0.0     0.0     0.0     0.0     1.0   
L5 ET         1.0     1.0     1.0     0.0     0.0     0.0     0.0     0.0   
L5 IT         1.0     1.0     1.0     0.0     0.0     1.0     0.0     0.0   
L5/6 NP       0.0     1.0     1.0     0.0     0.0     0.0     0.0     0.0   
L6 CT         1.0     1.0     1.0     0.0     0.0     1.0     0.0     0.0   
L6 IT         1.0     1.0     1.0     0.0     0.0     1.0     0.0     0.0   
L6b           0.0     1.0     1.0     0.0     0.0     0.0     0.0     1.0   
Lamp5         0.0     1.0     1.0     0.0     1.0     0.0     1.0     1.0   
Micro-PVM     0.0     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/anndata/_core/anndata.py:117: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is t

bin_id     3094     3095     3112     3113     3119     3120     3121     \
cell_type                                                                  
Astro          0.0      0.0      0.0      0.0      0.0      0.0      0.0   
Endo           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
L2/3 IT        1.0      1.0      0.0      0.0      1.0      1.0      1.0   
L5 ET          1.0      1.0      0.0      0.0      1.0      1.0      1.0   
L5 IT          1.0      1.0      0.0      0.0      1.0      1.0      1.0   
L5/6 NP        0.0      0.0      0.0      0.0      1.0      1.0      1.0   
L6 CT          1.0      1.0      0.0      0.0      1.0      1.0      1.0   
L6 IT          1.0      1.0      0.0      0.0      1.0      1.0      1.0   
L6b            0.0      0.0      0.0      0.0      1.0      1.0      1.0   
Lamp5          0.0      0.0      1.0      1.0      1.0      1.0      1.0   
Micro-PVM      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
Oligo       

/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/anndata/_core/anndata.py:117: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is t

bin_id     30     31     32     33     34     35     36     37     38     \
cell_type                                                                  
Astro        0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    0.0   
Endo         0.0    0.0    0.0    0.0    0.0    1.0    0.0    0.0    0.0   
L2/3 IT      1.0    1.0    1.0    1.0    1.0    0.0    1.0    0.0    0.0   
L5 ET        1.0    1.0    1.0    1.0    1.0    0.0    1.0    0.0    0.0   
L5 IT        1.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0   
L5/6 NP      0.0    1.0    0.0    1.0    1.0    1.0    1.0    0.0    0.0   
L6 CT        1.0    1.0    1.0    1.0    1.0    0.0    1.0    1.0    1.0   
L6 IT        1.0    1.0    1.0    1.0    1.0    0.0    1.0    1.0    0.0   
L6b          0.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0   
Lamp5        0.0    1.0    1.0    1.0    1.0    1.0    1.0    1.0    0.0   
Micro-PVM    0.0    0.0    1.0    0.0    0.0    0.0    0.0    0.0    0.0   
Oligo       

/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/anndata/_core/anndata.py:117: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is t

bin_id     12    13    14    15    16    17    18    19    20    21    ...  \
cell_type                                                              ...   
Astro       0.0   0.0   1.0   0.0   0.0   1.0   1.0   1.0   1.0   0.0  ...   
Endo        0.0   0.0   1.0   0.0   0.0   1.0   1.0   1.0   1.0   0.0  ...   
L2/3 IT     1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0  ...   
L5 ET       1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0  ...   
L5 IT       1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0  ...   
L5/6 NP     1.0   1.0   1.0   0.0   1.0   1.0   1.0   1.0   1.0   1.0  ...   
L6 CT       1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0  ...   
L6 IT       1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0  ...   
L6b         1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0  ...   
Lamp5       1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   1.0   0.0  ...   
Micro-PVM   0.0   1.0   0.0   0.0   0.0   0.0   0.0   1.0   1.0 

/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/anndata/_core/anndata.py:117: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-7-a859723120c3>:184: SettingWithCopyWarning: 
A value is t

In [20]:
#cross species correlation
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck




def calculate_pearson_correlation(df, df_b, corr_method):
    # Perform bin intersection
    bins_intersect = set(df.columns.tolist()).intersection(set(df_b.columns.tolist()))
    df = df.loc[:, bins_intersect]
    #df = df.fillna(0)
    #df_b = df_b.fillna(0)
    df_b = df_b.loc[:, bins_intersect]


    # Z-score normalization
    df_b_z = stats.zscore(df_b, axis=0, nan_policy='omit')
    df_b_z = pd.DataFrame(df_b_z, index=df_b.index.tolist(), columns=df_b.columns)
    df_b_z['cell_type'] = df_b_z.index.tolist()
    df_b_z = df_b_z.set_index(['cell_type'])

    df_z = stats.zscore(df, axis=0, nan_policy='omit')
    df_z = pd.DataFrame(df_z, index=df.index.tolist(), columns=df.columns)
    df_z['cell_type'] = df_z.index.tolist()
    df_z['cell_type'] = [x + '_hic' for x in df_z['cell_type']]
    df_z = df_z.set_index(['cell_type'])
    

    # Concatenate dataframes
    df_corr = pd.concat([df_b_z, df_z])

    
    
    #df_corr = df_corr.dropna(axis=1, how='all')
    #df_corr = df_corr.dropna(axis=1)
    
    #df_corr = df_corr.set_index(['cell_type'])

            
    #features_sc = stats.zscore(df_corr, axis=0, nan_policy='omit')
    
    #features_sc = features_sc.dropna(how='all', axis=1).fillna(0)
    
    #features_sc = features_sc.dropna(how='all', axis=1)
    
                
    #df_dist_df = features_sc.T.corr(min_periods=200, method=corr_method)
    df_dist_df = df_corr.T.corr(min_periods=10, method=corr_method)



    return df_dist_df


def calculate_auc_nan(df_dist_df, tp):
    df_jac_subset = df_dist_df.values
    df_exp_subset = tp.values

    coodinates_1 = np.where(np.isnan(df_jac_subset))
    coodinates_2 = np.where(np.isnan(df_exp_subset))

    x_coo = coodinates_1[0].tolist() + coodinates_2[0].tolist()
    y_coo = coodinates_1[1].tolist() + coodinates_2[1].tolist()

    df_jac_subset[x_coo, y_coo] = np.nan
    df_exp_subset[x_coo, y_coo] = np.nan

    predicts2 = bottleneck.nanrankdata(df_jac_subset, axis=1)

    tp = df_exp_subset.copy()
    tn = 1 - tp

    pos_rank_sum = tp * predicts2
    auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)

    df_auc = pd.DataFrame({'cell_type': df_dist_df.index.tolist(), 'AUC': auc_array})

    return df_auc


        

#for each marker-list and input file , I can make one output file

def calc_pair_corr(input_file_h5ad_a, input_file_h5ad_b, file_b_species, outputfile_h5ad, resolution, base_folder, SRP_name):

        adata = ad.read_h5ad(f'{input_file_h5ad_a}', backed='r')
        adata_b = ad.read_h5ad(f'{input_file_h5ad_b}', backed='r')
        df_b = adata_b.to_df()

        df = adata.to_df()

        cell_type_intersect = df.index.intersection(df_b.index)




        species_input='mouse'
        species_output='human'
        
        if file_b_species == 'mouse':
            species_input='mouse'
            species_output='human'
        else:
            species_input='human'
            species_output='mouse'
        
        full_input_path = f'{base_folder}/hi_c_data_processing/data_{species_input}/{SRP_name}/{resolution}/max/'
        
        full_target_path = f'{base_folder}/hi_c_data_processing/data_{species_output}/{SRP_name}/{resolution}/max/'
        if species_input=='mouse':
            chain_file = 'mm10ToHg38.over.chain.gz'
        else:
            chain_file = 'hg38ToMm10.over.chain.gz'
        for minmatch in [0.5]:

            #os.system(f"{base_folder}/hi_c_data_processing/software/liftOver -minMatch={minmatch} {full_input_path}/regions_bed_file.tsv {base_folder}/hi_c_data_processing/software/{chain_file} {full_input_path}/minmatch{minmatch}_{species_input}_to_{species_output}.bed u")

            #os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {full_input_path}/minmatch{minmatch}_{species_input}_to_{species_output}.bed -a {full_target_path}/regions_bed_file.tsv > {full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed")
            #os.system(f"bedtools intersect -wo -b {full_input_path}/minmatch{minmatch}_{species_input}_to_{species_output}.bed -a {full_target_path}/regions_bed_file.tsv > {full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed")

            if species_output=='human':

                df_human_mouse_bins = pd.read_csv(f'{full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed', sep='\t', names=['a', 'b', 'c', 'human_bin', 'a1', 'b1', 'c1', 'mouse_bin', 'overlap'])
            else:
                df_human_mouse_bins = pd.read_csv(f'{full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed', sep='\t', names=['a', 'b', 'c', 'mouse_bin', 'a1', 'b1', 'c1', 'human_bin', 'overlap'])

        #correct bin_id to correct bin_id

        df_human_mouse_bins['mouse_bin'] = [f"bin_{i}" for i in df_human_mouse_bins['mouse_bin'].tolist()]
        df_human_mouse_bins['human_bin'] = [f"bin_{i}" for i in df_human_mouse_bins['human_bin'].tolist()]


        dk_human = df.copy()
        dk_mouse = df_b.copy()

        df_human_mouse_bins  = df_human_mouse_bins[df_human_mouse_bins['mouse_bin'].isin(dk_mouse.T.index.tolist())]
        df_human_mouse_bins  = df_human_mouse_bins[df_human_mouse_bins['human_bin'].isin(dk_human.T.index.tolist())]
                

        np_of_col = len(cell_type_intersect)*2
        np_of_rows = len(cell_type_intersect)*2
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in ['mean']:


                                df = adata.to_df(layer=given_layer)

                                df = df.loc[cell_type_intersect,:]

                                df_b = adata_b.to_df(layer=given_layer)

                                df_b = df_b.loc[cell_type_intersect,:]


                                df = df.loc[:,df_human_mouse_bins['human_bin'].tolist()]

                                df = df.T
                                df.index = df_human_mouse_bins['mouse_bin'].tolist()
                                df = df.T
                                df_b = df_b.loc[:,df_human_mouse_bins['mouse_bin'].tolist()]




                                df_corr_real_names = calculate_pearson_correlation(df, df_b, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr_real_names

                                # Perform cell type intersection
                                #cell_type_intersect = df.index.intersection(df_b.index)

                                hic_cell_type = [x + '_hic' for x in cell_type_intersect]

                                df_corr = df_corr_real_names.loc[cell_type_intersect,:]
                            
                                df_corr = df_corr[hic_cell_type]

                                #df_corr  = df_corr.fillna(0)

                                #df_corr += abs(df_corr.min().min())

                                given_dict = dict(zip(df_corr.index.tolist(), df_corr.index.tolist()))

                                n = len(given_dict.keys())

                                tp_class = np.zeros((n, n))

                                # Fill the diagonal elements with 1
                                np.fill_diagonal(tp_class, 1)

                                df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

                                for key, value in given_dict.items():
                                    df_tp_class.loc[key, value] = 1
                            
                                df_tp_class = df_tp_class.loc[df_corr.index.tolist(), :]
                                    
                                    
                                df_exp = calculate_auc_nan(df_corr, df_tp_class)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = df_corr_real_names.index.tolist()
        adata_l.var_names = df_corr_real_names.columns.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")





In [ ]:

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
#no_of_markers_list = [200]   
for no_of_markers in no_of_markers_list:

    for species in ['human']:
        for process_type in ['intra']:
            for resolution in ['1kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                                dist = 0
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'

                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                                    
                                #input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{process_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                
                                
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_cross_species_overlap.h5ad'


                                #input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_cross_species.h5ad'

                                if species == 'human':
                                    species_b = 'mouse'
                                #input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{process_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                               
                                #calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, marker_name)
                                if os.path.isfile(outputfile_h5ad):
                                    pass
                                else:
                                    calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, resolution, base_folder, SRP_name)


<ipython-input-9-a8138fb5ed22>:106: RuntimeWarning: invalid value encountered in true_divide
  auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)


In [21]:

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
#no_of_markers_list = [200]   
for no_of_markers in no_of_markers_list:

    for species in ['human']:
        for process_type in ['inter']:
            for resolution in ['1kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                                dist = 0
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='none'

                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                                    
                                #input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{process_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                
                                
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_cross_species_overlap.h5ad'


                                #input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_cross_species.h5ad'

                                if species == 'human':
                                    species_b = 'mouse'
                                #input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{process_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                               
                                #calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, marker_name)
                                if os.path.isfile(outputfile_h5ad):
                                    pass
                                else:
                                    calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, resolution, base_folder, SRP_name)


In [23]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck




def calculate_pearson_correlation(df, df_b, corr_method):
    # Perform bin intersection
    bins_intersect = set(df.columns.tolist()).intersection(set(df_b.columns.tolist()))
    df = df.loc[:, bins_intersect]
    #df = df.fillna(0)
    #df_b = df_b.fillna(0)
    df_b = df_b.loc[:, bins_intersect]


    # Z-score normalization
    df_b_z = stats.zscore(df_b, axis=0, nan_policy='omit')
    df_b_z = pd.DataFrame(df_b_z, index=df_b.index.tolist(), columns=df_b.columns)
    df_b_z['cell_type'] = df_b_z.index.tolist()
    df_b_z = df_b_z.set_index(['cell_type'])

    df_z = stats.zscore(df, axis=0, nan_policy='omit')
    df_z = pd.DataFrame(df_z, index=df.index.tolist(), columns=df.columns)
    df_z['cell_type'] = df_z.index.tolist()
    df_z['cell_type'] = [x + '_hic' for x in df_z['cell_type']]
    df_z = df_z.set_index(['cell_type'])
    

    # Concatenate dataframes
    #print (df_b_z)
    #print (df_z)
    df_corr = pd.concat([df_b_z, df_z], axis=0)

    
    
    #df_corr = df_corr.dropna(axis=1, how='all')
    #df_corr = df_corr.dropna(axis=1)
    
    #df_corr = df_corr.set_index(['cell_type'])

            
    #features_sc = stats.zscore(df_corr, axis=0, nan_policy='omit')
    
    #features_sc = features_sc.dropna(how='all', axis=1).fillna(0)
    
    #features_sc = features_sc.dropna(how='all', axis=1)
    
                
    df_dist_df = df_corr.T.corr(min_periods=10, method=corr_method)



    return df_dist_df


def calculate_auc_nan(df_dist_df, tp):
    df_jac_subset = df_dist_df.values
    df_exp_subset = tp.values

    coodinates_1 = np.where(np.isnan(df_jac_subset))
    coodinates_2 = np.where(np.isnan(df_exp_subset))

    x_coo = coodinates_1[0].tolist() + coodinates_2[0].tolist()
    y_coo = coodinates_1[1].tolist() + coodinates_2[1].tolist()

    df_jac_subset[x_coo, y_coo] = np.nan
    df_exp_subset[x_coo, y_coo] = np.nan

    predicts2 = bottleneck.nanrankdata(df_jac_subset, axis=1)

    tp = df_exp_subset.copy()
    tn = 1 - tp

    pos_rank_sum = tp * predicts2
    auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)

    df_auc = pd.DataFrame({'cell_type': df_dist_df.index.tolist(), 'AUC': auc_array})

    return df_auc

cell_type_map = {
 'Adipocyte' : 'Adipocytes',
 'Atrial Cardiomyocyte': 'Cardiomyocytes',
 'Ventricular Cardiomyocyte':'Immature_Cardiomyocytes',
 'Endothelial_Arterial': 'Endothelial' ,
 'Fibroblast': 'Fibroblasts',
 'Smooth Muscle': 'Smooth_Muscle_Cells',
 'Lymphocyte': 'Lymphoid_Immune_Cells',
 'Macrophage': 'Myeloid_Immune_Cells',
 'Nervous': 'Neuronal_Cells',}
        

#for each marker-list and input file , I can make one output file

def calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name):
    

        adata = ad.read_h5ad(f'{input_file_h5ad}', backed='r')
        adata_b = ad.read_h5ad(f'{input_file_another_exp_h5ad}', backed='r')
        df_b = adata_b.to_df()
        
        if marker_name == 'heart':
            df_b.index = [cell_type_map[x] for x in cell_type_map]

        df = adata.to_df()

        cell_type_intersect = df.index.intersection(df_b.index)


        df_b = df_b.loc[cell_type_intersect,:]
        

        np_of_col = len(cell_type_intersect)*2
        np_of_rows = len(cell_type_intersect)*2
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:
                        #for given_layer in accepted_layer_list:
                        
                    
                                df = adata.to_df(layer=given_layer)

                                df = df.loc[cell_type_intersect,:]

                                df_corr_real_names = calculate_pearson_correlation(df, df_b, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr_real_names

                                # Perform cell type intersection
                                #cell_type_intersect = df.index.intersection(df_b.index)

                                hic_cell_type = [x + '_hic' for x in cell_type_intersect]

                                df_corr = df_corr_real_names.loc[cell_type_intersect,:]
                            
                                df_corr = df_corr[hic_cell_type]

                                #df_corr  = df_corr.fillna(0)

                                #df_corr += abs(df_corr.min().min())

                                given_dict = dict(zip(df_corr.index.tolist(), df_corr.index.tolist()))

                                n = len(given_dict.keys())

                                tp_class = np.zeros((n, n))

                                # Fill the diagonal elements with 1
                                np.fill_diagonal(tp_class, 1)

                                df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

                                for key, value in given_dict.items():
                                    df_tp_class.loc[key, value] = 1
                            
                                df_tp_class = df_tp_class.loc[df_corr.index.tolist(), :]
                                    
                                df_exp = calculate_auc_nan(df_corr, df_tp_class)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = df_corr_real_names.index.tolist()
        adata_l.var_names = df_corr_real_names.columns.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")


In [26]:
no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
#no_of_markers_list = [200]
for no_of_markers in no_of_markers_list:
    for species in ['mouse']:
        for process_type in ['intra']:
            for resolution in ['1kbp_raw']:
                for shuf in [False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                            for dist in [0]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{process_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)



<ipython-input-23-d3a48018c785>:106: RuntimeWarning: invalid value encountered in true_divide
  auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)


In [27]:
no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
#no_of_markers_list = [200]
for no_of_markers in no_of_markers_list:
    for species in ['mouse', 'human']:
        for process_type in ['inter']:
            for resolution in ['1kbp_raw']:
                for shuf in [False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                            for dist in [0]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='none'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{process_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

